# Starbucks data analysis(crawling)

In [ ]:
# 스타벅스 데이터 분석(Crawling)
# 스타벅스 홈페이지 >> 전국 매장 정보(지도) >> 크롤링
# 서울시 열린 데이터 광장 >> Open API(Application Programming Interface) >> 서울시 데이터 활용
# Open API(Application Programming Interface): 데이터 분석을 위해 데이터를 제공할 수 있도록 만든 인터페이스

# 라이브러리 추가 설치: xlrd / openpyxl

In [19]:
from selenium import webdriver
from bs4 import BeautifulSoup
import pandas as pd
import time

browser = webdriver.Chrome("C:/mychrome/chromedriver.exe")
url = 'https://www.starbucks.co.kr/store/store_map.do?disp=locale'
browser.get(url)

# 서울시 버튼
seoulBtn = "#container > div > form > fieldset > div > section > article.find_store_cont > article > article:nth-child(4) > div.loca_step1 > div.loca_step1_cont > ul > li:nth-child(1) > a"
browser.find_element_by_css_selector(seoulBtn).click()
time.sleep(2)

# 전체 버튼
allBtn = "#mCSB_2_container > ul > li:nth-child(1) > a"
browser.find_element_by_css_selector(allBtn).click()
time.sleep(2)


In [76]:
# 현재 떠있는 html 파일을 가지고와서 읽어야해.
# 매장 리스트 정보(tag, 규칙 확인) 가져오기.
# 

html = browser.page_source  # browser의 소스코드를 모두 html에 저장.
soup = BeautifulSoup(html,'html.parser') 
starbucksSoupList = soup.select('li.quickResultLstCon')  # 모두 tag 이름이 같음.



In [71]:
# starbucksStore = starbucksSoupList[0]
# name = starbucksStore.select('strong')[0].getText('',1)
# lat = starbucksStore['data-lat'].strip()
# lng = starbucksStore['data-long'].strip()

# # starbucksStore.select('i')  # [<i class="pin_general">리저브 매장 2번</i>]
# # starbucksStore.select('i')[0]['class']  # ['pin_general']
# # starbucksStore.select('i')[0]['class'][0]  # 'pin_general'
# storeType = starbucksStore.select('i')[0]['class'][0][4:]  # 매장타입: general

# # starbucksStore.select('p')[0].getText('',1).split()  # split: 구분자를 지정하지 않으면 공백으로 자동 구분
# address = str(starbucksStore.select('p')[0]).split('<br/>')[0].split('>')[1]
# tel = str(starbucksStore.select('p')[0]).split('<br/>')[1].split('<')[0]


#### 매장 리스트 정보 추출

In [80]:
starbucksList = []

for i in starbucksSoupList:
    name = i.select('strong')[0].getText('',1)
    lat = i['data-lat'].strip()
    lng = i['data-long'].strip()
    storeType = i.select('i')[0]['class'][0][4:]
    address = str(i.select('p')[0]).split('<br/>')[0].split('>')[1]
    tel = str(i.select('p')[0]).split('<br/>')[1].split('<')[0]
    starbucksList.append([name, lat, lng, storeType, address, tel])


## DataFrame

In [84]:
columns = ['매장명','위도','경도','매장타입','주소','전화번호']

seoulStarbucksDf = pd.DataFrame(starbucksList, columns=columns)
# seoulStarbucksDf.head()  # 상위 5개 정보 출력  /  tail(): 하위 5개 정보 출력
# seoulStarbucksDf.info()  # null: 비어있음  /  non-null: 비어있지않아.
# Pandas에서 object는 string과 같다.

# dataframe >> excel

seoulStarbucksDf.to_excel("seoul_starbucks_list.xlsx",index=False)  # 엑셀로 출력 / 순번 삭제


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 522 entries, 0 to 521
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   매장명     522 non-null    object
 1   위도      522 non-null    object
 2   경도      522 non-null    object
 3   매장타입    522 non-null    object
 4   주소      522 non-null    object
 5   전화번호    522 non-null    object
dtypes: object(6)
memory usage: 24.6+ KB


# 서울시 인구 통계 불러오기

In [128]:
# My 인증키 
SEOUL_API_AUTH_KEY = '6553496e76646e6a3831755646475a'

# API 호출을 위한 URL 작성
url = 'http://openapi.seoul.go.kr:8088/{}/json/SdeTlSccoSigW/1/25/'.format(SEOUL_API_AUTH_KEY)  # 시작페이지 1 / 마지막페이지 25

import requests

result_dict = requests.get(url).json()  # 클라이언트 요청에 의해 정상적으로 반응함 <Response [200]>  //  Error가 4xx >> 주소가 잘못된 것  // Error 5xx : Internal Error >> 서버 에러
# json파일의 형식이 dictionary!!
result_data = result_dict['SdeTlSccoSigW']
result_data['row'][0]  # 도봉구 정보

data_list = result_data['row']
data_list  # 딕셔너리가 요소로 들어가있는 길이가 25인 리스트
sampleDf = pd.DataFrame(data_list)  # 딕셔너리를 dataframe으로 넣으면 Key가 1행에서 분류하는 행으로 변환
result_dict

{'SdeTlSccoSigW': {'list_total_count': 25,
  'RESULT': {'CODE': 'INFO-000', 'MESSAGE': '정상 처리되었습니다'},
  'row': [{'OBJECTID': 1.0,
    'SIG_CD': '11320',
    'SIG_KOR_NM': '도봉구',
    'SIG_ENG_NM': 'Dobong-gu',
    'ESRI_PK': 0.0,
    'LAT': '37.6658609',
    'LNG': '127.0317674'},
   {'OBJECTID': 2.0,
    'SIG_CD': '11380',
    'SIG_KOR_NM': '은평구',
    'SIG_ENG_NM': 'Eunpyeong-gu',
    'ESRI_PK': 1.0,
    'LAT': '37.6176125',
    'LNG': '126.9227004'},
   {'OBJECTID': 3.0,
    'SIG_CD': '11230',
    'SIG_KOR_NM': '동대문구',
    'SIG_ENG_NM': 'Dongdaemun-gu',
    'ESRI_PK': 2.0,
    'LAT': '37.5838012',
    'LNG': '127.0507003'},
   {'OBJECTID': 4.0,
    'SIG_CD': '11590',
    'SIG_KOR_NM': '동작구',
    'SIG_ENG_NM': 'Dongjak-gu',
    'ESRI_PK': 3.0,
    'LAT': '37.4965037',
    'LNG': '126.9443073'},
   {'OBJECTID': 5.0,
    'SIG_CD': '11545',
    'SIG_KOR_NM': '금천구',
    'SIG_ENG_NM': 'Geumcheon-gu',
    'ESRI_PK': 4.0,
    'LAT': '37.4600969',
    'LNG': '126.9001546'},
   {'OBJECTID': 6.0

In [137]:
# 서울시 구 단위 정보를 추출하는 서비스

def seoul_open_api_data(url, service):
    data_list = None
    try:
        result_dict = requests.get(url).json()
        result_data = result_dict[service]
        code = result_data['RESULT']['CODE']
        if code == 'INFO-000':
            data_list = result_data['row']
    except:
        pass
    return data_list

seoul_data_list = seoul_open_api_data(url, 'SdeTlSccoSigW')  # 서비스이름: SdeTlSccoSigW 등

if seoul_data_list == None:
    print('key Error')

else:
    print(seoul_data_list)



[{'OBJECTID': 1.0, 'SIG_CD': '11320', 'SIG_KOR_NM': '도봉구', 'SIG_ENG_NM': 'Dobong-gu', 'ESRI_PK': 0.0, 'LAT': '37.6658609', 'LNG': '127.0317674'}, {'OBJECTID': 2.0, 'SIG_CD': '11380', 'SIG_KOR_NM': '은평구', 'SIG_ENG_NM': 'Eunpyeong-gu', 'ESRI_PK': 1.0, 'LAT': '37.6176125', 'LNG': '126.9227004'}, {'OBJECTID': 3.0, 'SIG_CD': '11230', 'SIG_KOR_NM': '동대문구', 'SIG_ENG_NM': 'Dongdaemun-gu', 'ESRI_PK': 2.0, 'LAT': '37.5838012', 'LNG': '127.0507003'}, {'OBJECTID': 4.0, 'SIG_CD': '11590', 'SIG_KOR_NM': '동작구', 'SIG_ENG_NM': 'Dongjak-gu', 'ESRI_PK': 3.0, 'LAT': '37.4965037', 'LNG': '126.9443073'}, {'OBJECTID': 5.0, 'SIG_CD': '11545', 'SIG_KOR_NM': '금천구', 'SIG_ENG_NM': 'Geumcheon-gu', 'ESRI_PK': 4.0, 'LAT': '37.4600969', 'LNG': '126.9001546'}, {'OBJECTID': 6.0, 'SIG_CD': '11530', 'SIG_KOR_NM': '구로구', 'SIG_ENG_NM': 'Guro-gu', 'ESRI_PK': 5.0, 'LAT': '37.4954856', 'LNG': '126.858121'}, {'OBJECTID': 7.0, 'SIG_CD': '11110', 'SIG_KOR_NM': '종로구', 'SIG_ENG_NM': 'Jongno-gu', 'ESRI_PK': 6.0, 'LAT': '37.5990998'

In [138]:
# 일반화 함수를 이용하여 시군구 open api 호출
SEOUL_API_AUTH_KEY = '6553496e76646e6a3831755646475a'
# API 호출을 위한 URL 작성
sgg_url = 'http://openapi.seoul.go.kr:8088/{}/json/SdeTlSccoSigW/1/25/'.format(SEOUL_API_AUTH_KEY)
sgg_data_list = seoul_open_api_data(sgg_url, 'SdeTlSccoSigW')

sggDf = pd.DataFrame(data = sgg_data_list, columns=['SIG_CD','SIG_KOR_NM','LAT','LNG'])
sggDf.columns = ['시군구코드','시군구명','위도','경도']
sggDf.to_excel("seoul_sgg_list.xlsx", index=0)

In [142]:
# 일반화 함수를 이용하여 시군구 open api 호출
SEOUL_API_AUTH_KEY = '6553496e76646e6a3831755646475a'

pop_url = 'http://openapi.seoul.go.kr:8088/{}/json/octastatapi419/1/26/'.format(SEOUL_API_AUTH_KEY)
pop_data_list = seoul_open_api_data(pop_url, 'octastatapi419')
sgg_pop_df = pd.DataFrame(pop_data_list)
sgg_pop_df.head()
sgg_pop_df.info()





<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26 entries, 0 to 25
Data columns (total 14 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   GIGAN                  26 non-null     object
 1   JACHIGU                26 non-null     object
 2   SEDAE                  26 non-null     object
 3   GYE_1                  26 non-null     object
 4   NAMJA_1                26 non-null     object
 5   YEOJA_1                26 non-null     object
 6   GYE_2                  26 non-null     object
 7   NAMJA_2                26 non-null     object
 8   YEOJA_2                26 non-null     object
 9   GYE_3                  26 non-null     object
 10  NAMJA_3                26 non-null     object
 11  YEOJA_3                26 non-null     object
 12  SEDAEDANGINGU          26 non-null     object
 13  N_65SEISANGGORYEONGJA  26 non-null     object
dtypes: object(14)
memory usage: 3.0+ KB


In [169]:
sgg_pop_df_selected = sgg_pop_df[sgg_pop_df['JACHIGU'] != '합계']  # 자치구가 '합계'와 값이 같지 않냐?
sgg_pop_df_final = sgg_pop_df_selected[['JACHIGU','GYE_1']]  # 1개 추출: 대괄호 1 or 2쌍  /  2개 추출: 대괄호 2쌍
  # boolean 참조라고 한다!! 
# >> 합계를 제외한 나머지 값 추출
sgg_pop_df_final.columns=['시군구명','주민등록인구']
sgg_pop_df_final.to_excel('sgg_pop.xlsx',index=0)

# 서울시 동 별 사업체 현황 api 호출

In [196]:
SEOUL_API_AUTH_KEY = '6553496e76646e6a3831755646475a'
biz_url = 'http://openapi.seoul.go.kr:8088/{}/json/octastatapi104/1/450/'.format(SEOUL_API_AUTH_KEY)  # 8088: 포트번호!! 물리적인 통로는 1개인데 논리적인 통로는 65536개 있음(포트가 65535번까지). 
biz_data_list = seoul_open_api_data(biz_url, 'octastatapi104')
sgg_biz_df = pd.DataFrame(biz_data_list)

# 구 단위 사업체 소계 현황
sgg_biz_df_selected = sgg_biz_df[sgg_biz_df['DONG'] == '소계']

sgg_biz_df_final = sgg_biz_df_selected[['JACHIGU','GYE','SAEOPCHESU_1']]
sgg_biz_df_final.columns = ['시군구명','종사자수','사업체수']
sgg_biz_df_final = sgg_biz_df_final.reset_index(drop = 1)
sgg_biz_df_final.to_excel("sgg_biz.xlsx",index=0)


In [222]:
# 엑셀파일 불러오기(Pandas 사용)

seoul_starbucks = pd.read_excel("seoul_starbucks_list.xlsx")

seoul_starbucks.head()

매장명         위도          경도     매장타입                          주소  \
0  역삼아레나빌딩  37.501087  127.043069  general     서울특별시 강남구 언주로 425 (역삼동)   
1   논현역사거리  37.510178  127.022223  general    서울특별시 강남구 강남대로 538 (논현동)   
2  신사역성일빌딩  37.514132  127.020563  general    서울특별시 강남구 강남대로 584 (논현동)   
3   국기원사거리  37.499517  127.031495  general    서울특별시 강남구 테헤란로 125 (역삼동)   
4   스탈릿대치R  37.494668  127.062583  reserve  서울특별시 강남구 남부순환로 2947 (대치동)   

        전화번호 시군구명  
0  1522-3232  강남구  
1  1522-3232  강남구  
2  1522-3232  강남구  
3  1522-3232  강남구  
4  1522-3232  강남구

In [223]:
sgg_names = []
for addr in seoul_starbucks['주소']:
    sgg_names.append(addr.split()[1])

seoul_starbucks['시군구명'] = sgg_names
seoul_starbucks.to_excel('seoul_starbucks_list.xlsx', index = False)

# 데이터 병합

In [4]:
# 보고 싶은 데이터: 구 별로 스타벅스 매장 갯수
#                 스타벅스 매장 수
# 시군구명
# 강남구              200
# 금천구              29
# ...                 ...
# 피봇(pivot)함수: 피봇팅(특정 기준에 따른 데이터 요약)
# pandas는 2가지 함수 있음 pivot table, pivot

seoul_sgg = pd.read_excel('seoul_sgg_list.xlsx')
# >> 시군구코드	  시군구명  	위도	경도

seoul_starbucks = pd.read_excel('seoul_starbucks_list.xlsx')
# >> 매장명	 위도	경도	매장타입	주소	전화번호	시군구명

seoul_sgg = pd.read_excel('seoul_sgg_list.xlsx')
# >> 시군구코드	  시군구명  	위도	경도

seoul_starbucks = pd.read_excel('seoul_starbucks_list.xlsx')
# >> 매장명	 위도	경도	매장타입	주소	전화번호	시군구명

starbucks_sgg_count = seoul_starbucks.pivot_table(index = '시군구명', values = '매장명', aggfunc = 'count').rename(columns = {'매장명': '스타벅스_매장수'})  # 매장명 >> 스타벅스_매장수로 변경
starbucks_sgg_count = starbucks_sgg_count.drop(['67'])  # 특정 행 삭제 drop!
starbucks_sgg_count

# 병합
seoul_sgg = pd.merge(seoul_sgg, starbucks_sgg_count, how = 'left', on = '시군구명')  # 왼쪽이 기준이 되어 합치기(merge)
seoul_sgg_pop = pd.read_excel('sgg_pop.xlsx')
seoul_sgg = pd.merge(seoul_sgg, seoul_sgg_pop, how = 'left', on = '시군구명')
seoul_sgg_biz = pd.read_excel('sgg_biz.xlsx')
seoul_sgg = pd.merge(seoul_sgg,seoul_sgg_biz, how = 'left', on = '시군구명')
seoul_sgg.head()



시군구코드  시군구명         위도          경도  스타벅스_매장수   주민등록인구    종사자수   사업체수
0  11320   도봉구  37.665861  127.031767         2  371,095   68669  18455
1  11380   은평구  37.617612  126.922700         8  474,165   87693  24179
2  11230  동대문구  37.583801  127.050700         8  374,039  143858  32994
3  11590   동작구  37.496504  126.944307        11  407,966  103915  19609
4  11545   금천구  37.460097  126.900155        10  262,337  223058  30080

In [247]:
# 병합 결과를 파일로 저장
seoul_sgg.to_excel("seoul_sgg_stat.xlsx", index = 0)

 pip install folium
### GeoJson 타입 지도파일
  -. 위치 정보를 갖는 점을 기반으로 지형을 표현하기 위해 설계된 개방형 공개 표준 형식



In [7]:
import pandas as pd
import folium
import json
# 서울시 스타벅스 매장 목록
seoul_starbucks = pd.read_excel('seoul_starbucks_list.xlsx')
seoul_starbucks.head()


매장명         위도          경도     매장타입                          주소  \
0  역삼아레나빌딩  37.501087  127.043069  general     서울특별시 강남구 언주로 425 (역삼동)   
1   논현역사거리  37.510178  127.022223  general    서울특별시 강남구 강남대로 538 (논현동)   
2  신사역성일빌딩  37.514132  127.020563  general    서울특별시 강남구 강남대로 584 (논현동)   
3   국기원사거리  37.499517  127.031495  general    서울특별시 강남구 테헤란로 125 (역삼동)   
4   스탈릿대치R  37.494668  127.062583  reserve  서울특별시 강남구 남부순환로 2947 (대치동)   

        전화번호 시군구명  
0  1522-3232  강남구  
1  1522-3232  강남구  
2  1522-3232  강남구  
3  1522-3232  강남구  
4  1522-3232  강남구

In [64]:
# 37.501087	127.043069

starbucks_map = folium.Map(zoom_start=11, location=[37.573050, 126.979189], tiles = 'Stamen Terrain' )


In [65]:
# 데이터 프레임에서 자료를 참조하는 방법
##loc, iloc, ix... 와 같은 속성을 이용해서 데이터 프레임에 저장된 자료 참조 가능.

for idx in seoul_starbucks.index:
    lat = seoul_starbucks.loc[idx, '위도']
    lng = seoul_starbucks.loc[idx, '경도']
    folium.CircleMarker(
        location = [lat, lng],
        color = 'red',
        fill_color = 'red',
        fill_opacity = -1, # 투명도
        weight = 1,
        radius = 3
    ).add_to(starbucks_map)  # 클래스(.대문자)로부터 객체 생성
starbucks_map

In [19]:
'''
seoul_starbucks.loc[1]
seoul_starbucks.loc[1,'위도']
'''

37.510178

In [90]:
mymap = folium.Map(location=[37.573050, 126.979189], 
           zoom_start = 7, 
           tiles = 'stamen Terrain')

In [91]:
folium.Marker([37.573050, 126.979189],
              icon = folium.Icon(icon = 'cloud'),
              popup = 'Seoul').add_to(mymap)
folium.Marker([36.573050, 126.979189],
              icon = folium.Icon(icon = 'cloud'),
              popup = 'Seoul').add_to(mymap)
folium.Marker([35.573050, 126.979189],
              icon = folium.Icon(icon = 'cloud'),
              popup = 'Seoul').add_to(mymap)

mymap

In [94]:
# 37.501087	127.043069

starbucks_map = folium.Map(zoom_start=11,
                           location=[37.573050, 126.979189],
                           tiles = 'Stamen Terrain' )
for idx in seoul_starbucks.index:
    lat = seoul_starbucks.loc[idx, '위도']
    lng = seoul_starbucks.loc[idx, '경도']
    store_type = seoul_starbucks.loc[idx, '매장타입']
    
    fillColor = ''
    if store_type == 'general':
        fillColor = 'green'
        size = 2
    elif store_type == 'reserve':
        fillColor = 'blue'
        size = 3
    elif store_type == 'generalDT':
        fillColor = 'red'
        size = 4
            
    folium.CircleMarker(
        location = [lat, lng],
        color = fillColor,
        fill_color = fillColor,
        # fill_opacity = -1, # 불투명도
        weight = 1,
        radius = size
    ).add_to(starbucks_map)  # 클래스(.대문자)로부터 객체 생성
starbucks_map


#### 행정구역에 따른 분포도를 알기 힘들다 >> 버블맵 활용!


In [95]:
seoul_sgg_stat = pd.read_excel('seoul_sgg_stat.xlsx')
seoul_sgg_stat

시군구코드  시군구명         위도          경도  스타벅스_매장수   주민등록인구    종사자수   사업체수
0   11320   도봉구  37.665861  127.031767         2  371,095   68669  18455
1   11380   은평구  37.617612  126.922700         8  474,165   87693  24179
2   11230  동대문구  37.583801  127.050700         8  374,039  143858  32994
3   11590   동작구  37.496504  126.944307        11  407,966  103915  19609
4   11545   금천구  37.460097  126.900155        10  262,337  223058  30080
5   11530   구로구  37.495486  126.858121        10  449,187  210506  37445
6   11110   종로구  37.599100  126.986149        38  177,023  269106  40871
7   11305   강북구  37.646995  127.014716         5  342,669   69787  18654
8   11260   중랑구  37.595379  127.093967         7  431,283   99241  27287
9   11680   강남구  37.495985  127.066409        80  570,913  711278  73590
10  11500   강서구  37.565762  126.822656        16  578,257  199289  33273
11  11140    중구  37.557945  126.994190        52  138,102  423808  66190
12  11740   강동구  37.549208  127.146482        15  490,945  143061  30079
13  11215   광진구  37.548144  127.085753        15  386,292  123689  24531
14  11440   마포구  37.562291  126.908780        32  392,087  252534  36504
15  11650   서초구  37.476953  127.037810        46  432,888  439963  47061
16  11290   성북구  37.606991  127.023218        13  484,359  113893  24690
17  11350   노원구  37.655264  127.077120        13  614,603  114736  25827
18  11710   송파구  37.504853  127.114482        31  689,909  302517  45375
19  11410  서대문구  37.582037  126.935666        19  336,490  111615  19612
20  11470   양천구  37.527062  126.856153        15  504,928  119443  26297
21  11560  영등포구  37.520641  126.913924        34  440,863  362524  44512
22  11620   관악구  37.465399  126.943807        11  546,814  119180  26235
23  11200   성동구  37.550675  127.040962        11  316,113  162019  26130
24  11170   용산구  37.531101  126.981074        19  250,844  133446  21178

### Encoding
 - 모든 컴퓨터는 문자를 나타낼 때 이진수로 바꿔서 저장함.(인코딩)
 - ASCII방식
 - 한글: 인코딩 방식  EUC-KR >> CP949
 - 유니코드(표준 인코딩 방식): UTF8, UTF16, UTF32... 전세계 모든 문자를 유니코드로 나타낼 수 있음.
 - 파이썬은 기본적으로 문자를 유니코드로 저장함.
 - 파이썬: string(유니코드)
 

In [109]:
i='가'
len(i)  # 1이 나옴. 유니코드라서 length가 1 나온다.
len(bytearray('가','cp949'))  # 2가 나옴. 인코딩 방식에 따라 길이가 달라진다.
u = '가나다'
u.encode('cp949')
type(u.encode('cp949'))  # type이 bytes로 나옴.
u = u.encode('euc-kr')
u.decode('euc-kr')  # '가나다'

'가나다'

In [135]:
sgg_geojson_file_path = 'seoul.geojson'  # key와 value의 쌍으로 이루어 짐
seoul_sgg_geo = json.load(open(sgg_geojson_file_path, encoding = 'utf-8'))  # json 파일 읽기 / encoding: 한글 깨짐 방지
seoul_sgg_geo


{'type': 'FeatureCollection',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'SIG_CD': '11320',
    'SIG_KOR_NM': '도봉구',
    'SIG_ENG_NM': 'Dobong-gu',
    'ESRI_PK': 0,
    'SHAPE_AREA': 0.00210990544544,
    'SHAPE_LEN': 0.239901251347},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[127.019851357, 37.70088490199998],
      [127.02217147700003, 37.69960736799999],
      [127.02341184299996, 37.69995983299998],
      [127.02533791899998, 37.69948105499998],
      [127.02692041600005, 37.70015310500003],
      [127.02704481599994, 37.70101150699998],
      [127.02771004600004, 37.70083744700003],
      [127.02823835, 37.700188083],
      [127.02833534499996, 37.70006885100003],
      [127.02901307699995, 37.69957318899998],
      [127.02930740500005, 37.699210467],
      [127.02962280199995, 37.69810365199999],
      [127.02967567200005, 37.69773805400001],
      [127.02975002699998, 37.

In [136]:
starbucks_bubble = folium.Map(
location = [37.573050, 126.979189],
    # tiles = 'CartoDB positron',
    tiles = 'CartoDB dark_matter',
    # tiles = 'CartoDB',
    
    zoom_start = 11
    
)
starbucks_bubble

In [137]:
# 시군구 경계 포함
def style_function(feature):
    return {'opacity' : 0.7,
           'weight' : 1,
           'color' : 'white',
           'fillOpacity' : 0,
           'dashArray' : '5.5'}

folium.GeoJson(
seoul_sgg_geo, 
style_function = style_function
).add_to(starbucks_bubble)

starbucks_bubble

In [138]:
starbucks_mean = int(seoul_sgg_stat['스타벅스_매장수'].mean())  # 서울 스타벅스 매장수 평균 20개

In [145]:
for idx in seoul_sgg_stat.index:
    lat = seoul_sgg_stat.loc[idx, '위도']
    lng = seoul_sgg_stat.loc[idx, '경도']
    count = seoul_sgg_stat.loc[idx, '스타벅스_매장수']
    if count > starbucks_mean:
        fillColor = 'red'
    else:
        fillColor = 'blue'
    folium.CircleMarker(
    location = [lat,lng],
        color = '#FFFF00',
        fill_color = fillColor,
        radius = count/2,
        fill_opacity = 0.7,
        weight = 2
    ).add_to(starbucks_bubble)
    
starbucks_bubble

In [164]:
# 구 별 인구 1만명당 스타벅스 매장 수 
# seoul_sgg_stat.info()
# # ['만명당_매장수'] 컬럼 추가
# # seoul_sgg_stat.info()에 따르면 주민등록인구가 object라서 int로 자료형 변환이 필요함.
# 판다스에서 .apply(pd.to_numeric)로도 숫자형으로 변경 가능함.
seoul_sgg_stat['주민등록인구'] = seoul_sgg_stat['주민등록인구'].str.replace(',','')

# 312,334 >> 문자 -> 숫자 변환
# 먼저 comma를 없앤다.
# x = "312.334"
# x.replace('.','')


AttributeError: Can only use .str accessor with string values!

In [172]:
seoul_sgg_stat['주민등록인구'] = seoul_sgg_stat['주민등록인구'].astype(int)
seoul_sgg_stat.info()
seoul_sgg_stat['만명당_매장수'] = seoul_sgg_stat['스타벅스_매장수']/(seoul_sgg_stat['주민등록인구']/10000)
seoul_sgg_stat['만명당_매장수']
seoul_sgg_stat

# 지금 이 과정을 Data Science에서는 특성공학(Feature Engineering)이라고 함.

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25 entries, 0 to 24
Data columns (total 9 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   시군구코드     25 non-null     int64  
 1   시군구명      25 non-null     object 
 2   위도        25 non-null     float64
 3   경도        25 non-null     float64
 4   스타벅스_매장수  25 non-null     int64  
 5   주민등록인구    25 non-null     int32  
 6   종사자수      25 non-null     int64  
 7   사업체수      25 non-null     int64  
 8   만명당_매장수   25 non-null     float64
dtypes: float64(3), int32(1), int64(4), object(1)
memory usage: 1.8+ KB


시군구코드  시군구명         위도          경도  스타벅스_매장수  주민등록인구    종사자수   사업체수  \
0   11320   도봉구  37.665861  127.031767         2  371095   68669  18455   
1   11380   은평구  37.617612  126.922700         8  474165   87693  24179   
2   11230  동대문구  37.583801  127.050700         8  374039  143858  32994   
3   11590   동작구  37.496504  126.944307        11  407966  103915  19609   
4   11545   금천구  37.460097  126.900155        10  262337  223058  30080   
5   11530   구로구  37.495486  126.858121        10  449187  210506  37445   
6   11110   종로구  37.599100  126.986149        38  177023  269106  40871   
7   11305   강북구  37.646995  127.014716         5  342669   69787  18654   
8   11260   중랑구  37.595379  127.093967         7  431283   99241  27287   
9   11680   강남구  37.495985  127.066409        80  570913  711278  73590   
10  11500   강서구  37.565762  126.822656        16  578257  199289  33273   
11  11140    중구  37.557945  126.994190        52  138102  423808  66190   
12  11740   강동구  37.549208  127.146482        15  490945  143061  30079   
13  11215   광진구  37.548144  127.085753        15  386292  123689  24531   
14  11440   마포구  37.562291  126.908780        32  392087  252534  36504   
15  11650   서초구  37.476953  127.037810        46  432888  439963  47061   
16  11290   성북구  37.606991  127.023218        13  484359  113893  24690   
17  11350   노원구  37.655264  127.077120        13  614603  114736  25827   
18  11710   송파구  37.504853  127.114482        31  689909  302517  45375   
19  11410  서대문구  37.582037  126.935666        19  336490  111615  19612   
20  11470   양천구  37.527062  126.856153        15  504928  119443  26297   
21  11560  영등포구  37.520641  126.913924        34  440863  362524  44512   
22  11620   관악구  37.465399  126.943807        11  546814  119180  26235   
23  11200   성동구  37.550675  127.040962        11  316113  162019  26130   
24  11170   용산구  37.531101  126.981074        19  250844  133446  21178   

     만명당_매장수  
0   0.053895  
1   0.168718  
2   0.213881  
3   0.269630  
4   0.381189  
5   0.222624  
6   2.146614  
7   0.145913  
8   0.162306  
9   1.401264  
10  0.276694  
11  3.765333  
12  0.305533  
13  0.388307  
14  0.816145  
15  1.062631  
16  0.268396  
17  0.211519  
18  0.449335  
19  0.564653  
20  0.297072  
21  0.771215  
22  0.201165  
23  0.347977  
24  0.757443

In [177]:
sgg_geojson_file_path = 'seoul.geojson'  # key와 value의 쌍으로 이루어 짐
seoul_sgg_geo = json.load(open(sgg_geojson_file_path, encoding = 'utf-8'))
vizMap = folium.Map(
location = [37.573050, 126.979189],
    tiles = 'CartoDB dark_matter', 
    zoom_start = 11
)
def style_function(feature):
    return {'opacity' : 0.7,
           'weight' : 1,
           'color' : 'white',
           'fillOpacity' : 0}

folium.GeoJson(
seoul_sgg_geo, 
style_function = style_function
).add_to(vizMap)

# 만명당 매장수를 기반으로 시각화
top = seoul_sgg_stat['만명당_매장수'].quantile(0.9)  # quantile: 만명당_매장수를 오름차순으로 정렬(작->큰)된 
# 결과에서 90% 지점 추출 >> 분위수 얻어낼 때(0.25 >> 1, 4분위)

for idx in seoul_sgg_stat.index:
    lat = seoul_sgg_stat.loc[idx, '위도']
    lng = seoul_sgg_stat.loc[idx, '경도']
    r = seoul_sgg_stat.loc[idx, '만명당_매장수']
    if r > top:
        fillColor = 'red'
    else:
        fillColor = 'green'
    folium.CircleMarker(
    location = [lat,lng],
        color = '#FFFF00',
        fill_color = fillColor,
        radius = r*10,
        fill_opacity = 0.7,
        weight = 1.5
    ).add_to(vizMap)
    
vizMap




In [178]:
# 지도 데이터
# map 객체 생성
# 처음에는 서울 중심 좌표로 지도 출력
# 스타일 지정
# 

In [179]:
# 스타벅스 매장 갯수와 사업체 수(종사자 수)와 비교해서 출력.
